In [4]:
import pandas as pd
import numpy as np
import requests
import os
import tweepy
import json

## Gather the Data

Sources:

* CSV
* website
* Twitter API's JSON data to TXT

Resolved a [tweepy installation issue](https://stackoverflow.com/questions/38739694/install-python-package-package-missing-in-current-win-64-channels).

In [46]:
archive_df = pd.read_csv('twitter-archive-enhanced.csv')
archive_df.sample(5)

tweet_id  in_reply_to_status_id  in_reply_to_user_id  \
1035  744995568523612160                    NaN                  NaN   
163   860276583193509888                    NaN                  NaN   
101   872668790621863937                    NaN                  NaN   
1467  694329668942569472                    NaN                  NaN   
1010  747461612269887489                    NaN                  NaN   

                      timestamp  \
1035  2016-06-20 20:49:19 +0000   
163   2017-05-04 23:34:55 +0000   
101   2017-06-08 04:17:07 +0000   
1467  2016-02-02 01:21:07 +0000   
1010  2016-06-27 16:08:30 +0000   

                                                 source  \
1035  <a href="http://twitter.com/download/iphone" r...   
163   <a href="http://twitter.com/download/iphone" r...   
101   <a href="http://twitter.com/download/iphone" r...   
1467  <a href="http://twitter.com/download/iphone" r...   
1010  <a href="http://twitter.com/download/iphone" r...   

                                                   text  retweeted_status_id  \
1035  This is Abby. She got her face stuck in a glas...                  NaN   
163   This is Jordy. He likes to go on adventures an...                  NaN   
101   RT @loganamnosis: Penelope here is doing me qu...         8.726576e+17   
1467  Meet Grady. He's very hungry. Too bad no one c...                  NaN   
1010  Never seen a shark hold another shark like thi...                  NaN   

      retweeted_status_user_id retweeted_status_timestamp  \
1035                       NaN                        NaN   
163                        NaN                        NaN   
101                154767397.0  2017-06-08 03:32:35 +0000   
1467                       NaN                        NaN   
1010                       NaN                        NaN   

                                          expanded_urls  rating_numerator  \
1035  https://twitter.com/dog_rates/status/744995568...                 9   
163   https://twitter.com/dog_rates/status/860276583...                12   
101   https://twitter.com/loganamnosis/status/872657...                14   
1467  https://twitter.com/dog_rates/status/694329668...                 9   
1010  https://twitter.com/dog_rates/status/747461612...                10   

      rating_denominator   name doggo floofer  pupper  puppo  
1035                  10   Abby  None    None    None  puppo  
163                   10  Jordy  None    None    None   None  
101                   10   None  None    None    None   None  
1467                  10  Grady  None    None  pupper   None  
1010                  10   None  None    None    None   None

In [30]:
url = 'https://d17h27t6h515a5.cloudfront.net/topher/2017/August/599fd2ad_image-predictions/image-predictions.tsv'
response = requests.get(url)
response

<Response [200]>

In [31]:
folder = 'image-predictions'
if not os.path.exists(folder):
    os.makedirs(folder)

In [32]:
with open(os.path.join(folder, url.split('/')[-1]), mode='wb') as file:
    file.write(response.content)
    
os.listdir(folder)

['image-predictions.tsv']

In [33]:
img_predictions_df = pd.read_csv(folder + '/image-predictions.tsv', sep='\t')
img_predictions_df.head()

tweet_id                                          jpg_url  \
0  666020888022790149  https://pbs.twimg.com/media/CT4udn0WwAA0aMy.jpg   
1  666029285002620928  https://pbs.twimg.com/media/CT42GRgUYAA5iDo.jpg   
2  666033412701032449  https://pbs.twimg.com/media/CT4521TWwAEvMyu.jpg   
3  666044226329800704  https://pbs.twimg.com/media/CT5Dr8HUEAA-lEu.jpg   
4  666049248165822465  https://pbs.twimg.com/media/CT5IQmsXIAAKY4A.jpg   

   img_num                      p1   p1_conf p1_dog                  p2  \
0        1  Welsh_springer_spaniel  0.465074   True              collie   
1        1                 redbone  0.506826   True  miniature_pinscher   
2        1         German_shepherd  0.596461   True            malinois   
3        1     Rhodesian_ridgeback  0.408143   True             redbone   
4        1      miniature_pinscher  0.560311   True          Rottweiler   

    p2_conf p2_dog                   p3   p3_conf p3_dog  
0  0.156665   True    Shetland_sheepdog  0.061428   True  
1  0.074192   True  Rhodesian_ridgeback  0.072010   True  
2  0.138584   True           bloodhound  0.116197   True  
3  0.360687   True   miniature_pinscher  0.222752   True  
4  0.243682   True             Doberman  0.154629   True

**Hide these keys before publishing or sharing notebook.**

In [30]:
key = "XXXX"
key_secret = "XXXX"
token = "XX-XXXX"
token_secret = "XXXX"

auth = tweepy.OAuthHandler(key, key_secret)
auth.set_access_token(token, token_secret)

api = tweepy.API(auth)

I could skip over grabbing all the JSON data for each tweet and grab the `retweet_count` and `favorite_count` directly from the [status response](https://stackoverflow.com/questions/27900451/convert-tweepy-status-object-into-json#27901076). However, this project requires that I demonstrate how to [write JSON data to a file](http://stackabuse.com/reading-and-writing-json-to-a-file-in-python/), then load it into a pandas dataframe.

In [34]:
tweet_ids = list(archive_df.tweet_id)

tweet_data = {}
for tweet in tweet_ids:
    try:
        tweet_status = api.get_status(tweet, wait_on_rate_limit=True, wait_on_rate_limit_notify=True)
        tweet_data[str(tweet)] = tweet_status._json
        print(tweet_ids.index(tweet) + 1, "/", "2354")
    except:
        print("Error for: " + str(tweet))
        print(tweet_ids.index(tweet) + 1, "/", "2354")

1 / 2354
2 / 2354
3 / 2354
4 / 2354
5 / 2354
6 / 2354
7 / 2354
8 / 2354
9 / 2354
10 / 2354
11 / 2354
12 / 2354
13 / 2354
14 / 2354
15 / 2354
16 / 2354
17 / 2354
18 / 2354
19 / 2354
Error for: 888202515573088257
20 / 2354
21 / 2354
22 / 2354
23 / 2354
24 / 2354
25 / 2354
26 / 2354
27 / 2354
28 / 2354
29 / 2354
30 / 2354
31 / 2354
32 / 2354
33 / 2354
34 / 2354
35 / 2354
36 / 2354
37 / 2354
38 / 2354
39 / 2354
40 / 2354
41 / 2354
42 / 2354
43 / 2354
44 / 2354
45 / 2354
46 / 2354
47 / 2354
48 / 2354
49 / 2354
50 / 2354
51 / 2354
52 / 2354
53 / 2354
54 / 2354
55 / 2354
56 / 2354
57 / 2354
58 / 2354
59 / 2354
60 / 2354
61 / 2354
62 / 2354
63 / 2354
64 / 2354
65 / 2354
66 / 2354
67 / 2354
68 / 2354
69 / 2354
70 / 2354
71 / 2354
72 / 2354
73 / 2354
74 / 2354
75 / 2354
76 / 2354
77 / 2354
78 / 2354
79 / 2354
80 / 2354
81 / 2354
82 / 2354
83 / 2354
84 / 2354
85 / 2354
86 / 2354
87 / 2354
88 / 2354
89 / 2354
90 / 2354
91 / 2354
92 / 2354
93 / 2354
94 / 2354
95 / 2354
96 / 2354
97 / 2354
98 / 2354

In [35]:
with open('tweet_json.txt', 'w') as file:
    json.dump(tweet_data, file)

In [2]:
with open('tweet_json.txt') as file:
    data = json.load(file)

{'892420643555336193': {'contributors': None,
  'coordinates': None,
  'created_at': 'Tue Aug 01 16:23:56 +0000 2017',
  'entities': {'hashtags': [],
   'media': [{'display_url': 'pic.twitter.com/MgUWQ76dJU',
     'expanded_url': 'https://twitter.com/dog_rates/status/892420643555336193/photo/1',
     'id': 892420639486877696,
     'id_str': '892420639486877696',
     'indices': [86, 109],
     'media_url': 'http://pbs.twimg.com/media/DGKD1-bXoAAIAUK.jpg',
     'media_url_https': 'https://pbs.twimg.com/media/DGKD1-bXoAAIAUK.jpg',
     'sizes': {'large': {'h': 528, 'resize': 'fit', 'w': 540},
      'medium': {'h': 528, 'resize': 'fit', 'w': 540},
      'small': {'h': 528, 'resize': 'fit', 'w': 540},
      'thumb': {'h': 150, 'resize': 'crop', 'w': 150}},
     'type': 'photo',
     'url': 'https://t.co/MgUWQ76dJU'}],
   'symbols': [],
   'urls': [],
   'user_mentions': []},
  'extended_entities': {'media': [{'display_url': 'pic.twitter.com/MgUWQ76dJU',
     'expanded_url': 'https://twitte

In [26]:
df_list = []

for tweet_id in data.keys():
    retweets = data[tweet_id]['retweet_count']
    favorites = data[tweet_id]['favorite_count']# + data[tweet_id]['favourites_count']
    df_list.append({'tweet_id': tweet_id,
                        'retweets': retweets,
                        'favorites': favorites})

Why did `favourites_count` fail? Is `favourites_count` in every tweet's data?

In [35]:
tweets_df = pd.DataFrame(df_list, columns = ['tweet_id', 'retweets', 'favorites'])
tweets_df.sample(10)

tweet_id  retweets  favorites
1492  692423280028966913       263       1610
910   757354760399941633      1621       4969
1142  726935089318363137      2731       7464
485   813944609378369540      3707          0
1900  674606911342424069       113       1004
2034  671547767500775424       647       1436
590   798705661114773508      7674          0
256   843235543001513987      6803      23179
83    876484053909872640      2492      19067
1660  682750546109968385       491       1661

## Assessment

Three dataframes:
 * `tweets_df` which has retweet and favorite counts
 * `img_predictions_df` has the results a neural network trying to identify dog breed in a tweet's picture
 * `archve_df` has the tweet's text, rating, and dog category

In [36]:
tweets_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2351 entries, 0 to 2350
Data columns (total 3 columns):
tweet_id     2351 non-null object
retweets     2351 non-null int64
favorites    2351 non-null int64
dtypes: int64(2), object(1)
memory usage: 55.2+ KB


In [38]:
img_predictions_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2075 entries, 0 to 2074
Data columns (total 12 columns):
tweet_id    2075 non-null int64
jpg_url     2075 non-null object
img_num     2075 non-null int64
p1          2075 non-null object
p1_conf     2075 non-null float64
p1_dog      2075 non-null bool
p2          2075 non-null object
p2_conf     2075 non-null float64
p2_dog      2075 non-null bool
p3          2075 non-null object
p3_conf     2075 non-null float64
p3_dog      2075 non-null bool
dtypes: bool(3), float64(3), int64(2), object(4)
memory usage: 152.1+ KB


In [42]:
archive_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2356 entries, 0 to 2355
Data columns (total 17 columns):
tweet_id                      2356 non-null int64
in_reply_to_status_id         78 non-null float64
in_reply_to_user_id           78 non-null float64
timestamp                     2356 non-null object
source                        2356 non-null object
text                          2356 non-null object
retweeted_status_id           181 non-null float64
retweeted_status_user_id      181 non-null float64
retweeted_status_timestamp    181 non-null object
expanded_urls                 2297 non-null object
rating_numerator              2356 non-null int64
rating_denominator            2356 non-null int64
name                          2356 non-null object
doggo                         2356 non-null object
floofer                       2356 non-null object
pupper                        2356 non-null object
puppo                         2356 non-null object
dtypes: float64(4), int64(3), ob

In [47]:
img_predictions_df.describe()

tweet_id      img_num      p1_conf       p2_conf       p3_conf
count  2.075000e+03  2075.000000  2075.000000  2.075000e+03  2.075000e+03
mean   7.384514e+17     1.203855     0.594548  1.345886e-01  6.032417e-02
std    6.785203e+16     0.561875     0.271174  1.006657e-01  5.090593e-02
min    6.660209e+17     1.000000     0.044333  1.011300e-08  1.740170e-10
25%    6.764835e+17     1.000000     0.364412  5.388625e-02  1.622240e-02
50%    7.119988e+17     1.000000     0.588230  1.181810e-01  4.944380e-02
75%    7.932034e+17     1.000000     0.843855  1.955655e-01  9.180755e-02
max    8.924206e+17     4.000000     1.000000  4.880140e-01  2.734190e-01

In [48]:
archive_df.describe()

tweet_id  in_reply_to_status_id  in_reply_to_user_id  \
count  2.356000e+03           7.800000e+01         7.800000e+01   
mean   7.427716e+17           7.455079e+17         2.014171e+16   
std    6.856705e+16           7.582492e+16         1.252797e+17   
min    6.660209e+17           6.658147e+17         1.185634e+07   
25%    6.783989e+17           6.757419e+17         3.086374e+08   
50%    7.196279e+17           7.038708e+17         4.196984e+09   
75%    7.993373e+17           8.257804e+17         4.196984e+09   
max    8.924206e+17           8.862664e+17         8.405479e+17   

       retweeted_status_id  retweeted_status_user_id  rating_numerator  \
count         1.810000e+02              1.810000e+02       2356.000000   
mean          7.720400e+17              1.241698e+16         13.126486   
std           6.236928e+16              9.599254e+16         45.876648   
min           6.661041e+17              7.832140e+05          0.000000   
25%           7.186315e+17              4.196984e+09         10.000000   
50%           7.804657e+17              4.196984e+09         11.000000   
75%           8.203146e+17              4.196984e+09         12.000000   
max           8.874740e+17              7.874618e+17       1776.000000   

       rating_denominator  
count         2356.000000  
mean            10.455433  
std              6.745237  
min              0.000000  
25%             10.000000  
50%             10.000000  
75%             10.000000  
max            170.000000

In [49]:
tweets_df.describe()

retweets      favorites
count   2351.000000    2351.000000
mean    3131.396852    8111.893662
std     5238.522870   11989.498195
min        0.000000       0.000000
25%      617.000000    1419.000000
50%     1453.000000    3594.000000
75%     3622.500000   10115.500000
max    79007.000000  132170.000000

### Issues

* `tweet_id` is int in `img_predictions_df` and `archive_df`
* `tweet_id` is str in `tweets_df`
* `timestamp` is str
* dog categories hide category variable
* dog categories are str
* `retweets` and `favorites` in their own table
* missing retweet and favorite data for some tweets
* outliers in `rating_numerator` and `rating_denominator`